In [1]:
import matplotlib.pyplot as plt

from time import sleep
import time
from playsound import playsound
import numpy as np
import matplotlib.pyplot as plt
import os
from datetime import datetime, timedelta

import queue
from portilooplot.jupyter_plot import ProgressPlot

from frontend import Frontend
from leds import LEDs, Color

from IPython.display import clear_output

In [2]:
DEFAULT_FRONTEND_CONFIG = [
    # nomenclature: name [default setting] [bits 7-0] : description
    # Read only ID:
    0x3E, # ID [xx] [REV_ID[2:0], 1, DEV_ID[1:0], NU_CH[1:0]] : (RO)
    # Global Settings Across Channels:
    0x96, # CONFIG1 [96] [1, DAISY_EN(bar), CLK_EN, 1, 0, DR[2:0]] : Datarate = 250 SPS
    0xC0, # CONFIG2 [C0] [1, 1, 0, INT_CAL, 0, CAL_AMP0, CAL_FREQ[1:0]] : No tests
    0x60, # CONFIG3 [60] [PD_REFBUF(bar), 1, 1, BIAS_MEAS, BIASREF_INT, PD_BIAS(bar), BIAS_LOFF_SENS, BIAS_STAT] : Power-down reference buffer, no bias
    0x00, # LOFF [00] [COMP_TH[2:0], 0, ILEAD_OFF[1:0], FLEAD_OFF[1:0]] : No lead-off
    # Channel-Specific Settings:
    0x61, # CH1SET [61] [PD1, GAIN1[2:0], SRB2, MUX1[2:0]] : Channel 1 active, 24 gain, no SRB2 & input shorted
    0x61, # CH2SET [61] [PD2, GAIN2[2:0], SRB2, MUX2[2:0]] : Channel 2 active, 24 gain, no SRB2 & input shorted
    0x61, # CH3SET [61] [PD3, GAIN3[2:0], SRB2, MUX3[2:0]] : Channel 3 active, 24 gain, no SRB2 & input shorted
    0x61, # CH4SET [61] [PD4, GAIN4[2:0], SRB2, MUX4[2:0]] : Channel 4 active, 24 gain, no SRB2 & input shorted
    0x61, # CH5SET [61] [PD5, GAIN5[2:0], SRB2, MUX5[2:0]] : Channel 5 active, 24 gain, no SRB2 & input shorted
    0x61, # CH6SET [61] [PD6, GAIN6[2:0], SRB2, MUX6[2:0]] : Channel 6 active, 24 gain, no SRB2 & input shorted
    0x61, # CH7SET [61] [PD7, GAIN7[2:0], SRB2, MUX7[2:0]] : Channel 7 active, 24 gain, no SRB2 & input shorted
    0x61, # CH8SET [61] [PD8, GAIN8[2:0], SRB2, MUX8[2:0]] : Channel 8 active, 24 gain, no SRB2 & input shorted
    0x00, # BIAS_SENSP [00] [BIASP8, BIASP7, BIASP6, BIASP5, BIASP4, BIASP3, BIASP2, BIASP1] : No bias
    0x00, # BIAS_SENSN [00] [BIASN8, BIASN7, BIASN6, BIASN5, BIASN4, BIASN3, BIASN2, BIASN1] No bias
    0x00, # LOFF_SENSP [00] [LOFFP8, LOFFP7, LOFFP6, LOFFP5, LOFFP4, LOFFP3, LOFFP2, LOFFP1] : No lead-off
    0x00, # LOFF_SENSN [00] [LOFFM8, LOFFM7, LOFFM6, LOFFM5, LOFFM4, LOFFM3, LOFFM2, LOFFM1] : No lead-off
    0x00, # LOFF_FLIP [00] [LOFF_FLIP8, LOFF_FLIP7, LOFF_FLIP6, LOFF_FLIP5, LOFF_FLIP4, LOFF_FLIP3, LOFF_FLIP2, LOFF_FLIP1] : No lead-off flip
    # Lead-Off Status Registers (Read-Only Registers):
    0x00, # LOFF_STATP [00] [IN8P_OFF, IN7P_OFF, IN6P_OFF, IN5P_OFF, IN4P_OFF, IN3P_OFF, IN2P_OFF, IN1P_OFF] : Lead-off positive status (RO)
    0x00, # LOFF_STATN [00] [IN8M_OFF, IN7M_OFF, IN6M_OFF, IN5M_OFF, IN4M_OFF, IN3M_OFF, IN2M_OFF, IN1M_OFF] : Laed-off negative status (RO)
    # GPIO and OTHER Registers:
    0x0F, # GPIO [0F] [GPIOD[4:1], GPIOC[4:1]] : All GPIOs as inputs
    0x00, # MISC1 [00] [0, 0, SRB1, 0, 0, 0, 0, 0] : Disable SRBM
    0x00, # MISC2 [00] [00] : Unused
    0x00, # CONFIG4 [00] [0, 0, 0, 0, SINGLE_SHOT, 0, PD_LOFF_COMP(bar), 0] : Single-shot, lead-off comparator disabled
]

FRONTEND_CONFIG = [
    0x3E, # ID (RO)
    0x95, # CONFIG1 [95] [1, DAISY_EN(bar), CLK_EN, 1, 0, DR[2:0]] : Datarate = 500 SPS
    0xD0, # CONFIG2 [C0] [1, 1, 0, INT_CAL, 0, CAL_AMP0, CAL_FREQ[1:0]]
    0xF0, # CONFIG3 [E0] [PD_REFBUF(bar), 1, 1, BIAS_MEAS, BIASREF_INT, PD_BIAS(bar), BIAS_LOFF_SENS, BIAS_STAT] : Power-down reference buffer, no bias
    0x00, # No lead-off
    0x03, # CH1SET [60] [PD1, GAIN1[2:0], SRB2, MUX1[2:0]] test signal
    0x02, # CH2SET
    0x00, # CH3SET
    0x03, # CH4SET voltage DVDD / 4
    0x03, # CH5SET voltage 0.5 × (AVDD + AVSS)
    0x03, # CH6SET
    0x05, # CH7SET test
    0x04, # CH8SET temperature
    0x00, # BIAS_SENSP
    0x00, # BIAS_SENSN
    0xFF, # LOFF_SENSP Lead-off on all positive pins?
    0xFF, # LOFF_SENSN Lead-off on all negative pins?
    0x00, # Normal lead-off
    0x00, # Lead-off positive status (RO)
    0x00, # Lead-off negative status (RO)
    0x00, # All GPIOs as output ?
    0x20, # Enable SRB1
]

frontend = Frontend()
leds = LEDs()

In [3]:
leds.led2(Color.PURPLE)
leds.aquisition(True)

In [4]:
class LiveDisplay():
    def __init__(self, datapoint_dim=8, window_len=100):
        self.datapoint_dim = datapoint_dim
        self.queue = [queue.Queue()] * datapoint_dim

        self.pp = ProgressPlot(plot_names=[f"channel#{i+1}" for i in range(datapoint_dim)], max_window_len=window_len)

    def add_datapoint(self, datapoint, filter=None):

        assert len(datapoint) == self.datapoint_dim
        disp_list = []
        for idx, point in enumerate(datapoint):
            if self.queue[idx].full():
                _ = self.queue[idx].get()
            if filter is not None:
                point = filter(point)
            if idx == 7:  # temperature sensor
                point = (point * 1000000.0 - 145300) / 490 + 25
                point = int(point)
#             if idx == 3:
#                 print(f"point 4: {point}")
#             if idx == 4:
#                 print(f"point 5: {point}")
            if idx == 6:
                print(f"test 7: {point * 2400}")
            self.queue[idx].put(point)
            disp_list.append([point])
#         disp_list.reverse()
        self.pp.update(disp_list)

In [5]:
def filter_24(value):
    return (value * 4.5) / (2**23 - 1)  # 23 because 1 bit is lost for sign

In [6]:
def filter_2scomplement(value):
    if (value & (1 << 23)) != 0:
        value = value - (1 << 24)
    return filter_24(value)

In [7]:
filter_2scomplement(8388607)

4.5

In [8]:
try:
    data = frontend.read_regs(0x00, 1)
    assert data == [0x3E], "Wrong output"
    print("EEG Frontend responsive")
    leds.led2(Color.BLUE)

    print("Configuring EEG Frontend")
    frontend.write_regs(0x00, FRONTEND_CONFIG)
    #config = DEFAULT_FRONTEND_CONFIG[:]
    #config[0x02] = 0xD0 # Activate test signals
    #config[0x03] = 0xE0 # Power-up reference buffer
    #for i in range(0x05, 0x0D):
    #    config[i] = 0x05 # Channel active, 1 gain, no SRB2 & Test signal
    #frontend.write_regs(0x00, config)
    data = frontend.read_regs(0x00, len(FRONTEND_CONFIG))
    assert data == FRONTEND_CONFIG, f"Wrong config: {data} vs {FRONTEND_CONFIG}"
    frontend.start()
    print("EEG Frontend configured")
    leds.led2(Color.PURPLE)
    while not frontend.is_ready():
        pass
    print("Ready for data")

    # Set up of leds
    leds.aquisition(True)
    sleep(0.5)
    leds.aquisition(False)
    sleep(0.5)
    leds.aquisition(True)
    
    # Initialize Live Display for live visualisation of data 
    live_disp = LiveDisplay(window_len=500)

    START = datetime.now()
    freq = 250
    ts_len = 1 / freq
    prev_ts = time.time()
    
    while True:
        # Wait for frontend and for minimum time limit
        while not frontend.is_ready() and not time.time() - prev_ts >= ts_len:
            pass
        prev_ts = time.time()
        
        # Read values and display
        values = frontend.read()
        live_disp.add_datapoint(values.channels(), filter=filter_2scomplement)
#         print(type(values.channels()))
        
        # Wait until reading is fully ompleted
        while frontend.is_ready():
            pass
    
    leds.aquisition(False)

finally:
    frontend.close()
    leds.close()

EEG Frontend responsive
Configuring EEG Frontend
EEG Frontend configured
Ready for data


<IPython.core.display.Javascript object>

test 7: 3.4091953526968184
test 7: 3.4156326550999467
test 7: 3.4091953526968184
test 7: 3.4156326550999467
test 7: 3.410482813177444
test 7: 3.4169201155805724
test 7: 3.4091953526968184
test 7: 3.4079078922161927
test 7: 3.410482813177444
test 7: 3.4079078922161927
test 7: 3.4117702736580697
test 7: 3.4130577341386954
test 7: 3.410482813177444
test 7: 3.4194950365418237
test 7: 3.4169201155805724
test 7: 3.410482813177444
test 7: 3.4091953526968184
test 7: -5.582428643992977
test 7: -5.586291025434854
test 7: -5.583716104473603
test 7: -5.579853723031726
test 7: -5.585003564954229
test 7: -5.588865946396106
test 7: -5.590153406876731
test 7: -5.579853723031726
test 7: -5.579853723031726
test 7: -5.595303248799234
test 7: -5.582428643992977
test 7: -5.579853723031726
test 7: -5.583716104473603
test 7: -5.585003564954229
test 7: -5.579853723031726
test 7: -5.591440867357357
test 7: -5.583716104473603
test 7: -5.583716104473603
test 7: -5.585003564954229
test 7: -5.581141183512352
test 

test 7: 3.4156326550999467
test 7: 3.4194950365418237
test 7: 3.410482813177444
test 7: 3.4091953526968184
test 7: 3.422069957503075
test 7: 3.410482813177444
test 7: 3.4130577341386954
test 7: 3.4130577341386954
test 7: 3.4156326550999467
test 7: 3.4130577341386954
test 7: 3.4130577341386954
test 7: 3.4117702736580697
test 7: 3.4130577341386954
test 7: 3.410482813177444
test 7: 3.4130577341386954
test 7: 3.4156326550999467
test 7: 3.410482813177444
test 7: 3.4091953526968184
test 7: 3.422069957503075
test 7: 3.410482813177444
test 7: 3.410482813177444
test 7: 3.4117702736580697
test 7: -5.588865946396106
test 7: -5.586291025434854
test 7: -5.582428643992977
test 7: -5.579853723031726
test 7: -5.590153406876731
test 7: -5.582428643992977
test 7: -5.577278802070475
test 7: -5.582428643992977
test 7: -5.583716104473603
test 7: -5.590153406876731
test 7: -5.582428643992977
test 7: -5.588865946396106
test 7: -5.585003564954229
test 7: -5.582428643992977
test 7: -5.586291025434854
test 7: -

test 7: -5.579853723031726
test 7: -5.586291025434854
test 7: -5.58757848591548
test 7: -5.582428643992977
test 7: -5.579853723031726
test 7: -5.586291025434854
test 7: -5.586291025434854
test 7: -5.586291025434854
test 7: -5.585003564954229
test 7: -5.579853723031726
test 7: -5.586291025434854
test 7: -5.583716104473603
test 7: -5.579853723031726
test 7: -5.582428643992977
test 7: -5.583716104473603
test 7: 3.410482813177444
test 7: 3.4169201155805724
test 7: 3.406620431735567
test 7: 3.4117702736580697
test 7: 3.4130577341386954
test 7: 3.4079078922161927
test 7: 3.406620431735567
test 7: 3.4040455107743157
test 7: 3.4130577341386954
test 7: 3.4169201155805724
test 7: 3.4169201155805724
test 7: 3.4130577341386954
test 7: 3.406620431735567
test 7: 3.414345194619321
test 7: 3.414345194619321
test 7: 3.4156326550999467
test 7: 3.4130577341386954
test 7: 3.410482813177444
test 7: 3.414345194619321
test 7: 3.4130577341386954
test 7: 3.4091953526968184
test 7: -4.083824644544679
test 7: -5

...

test 7: -5.582428643992977
test 7: -5.586291025434854
test 7: -5.583716104473603
test 7: -5.592728327837983
test 7: -5.582428643992977
test 7: -5.583716104473603
test 7: -5.581141183512352
test 7: -5.588865946396106
test 7: -5.58757848591548
test 7: -5.585003564954229
test 7: -5.577278802070475
test 7: -5.590153406876731
test 7: -5.585003564954229
test 7: -5.582428643992977
test 7: -5.586291025434854
test 7: -5.583716104473603
test 7: -5.583716104473603
test 7: -5.585003564954229
test 7: -5.582428643992977
test 7: 3.4194950365418237
test 7: 3.4091953526968184
test 7: 3.4169201155805724
test 7: 3.4130577341386954
test 7: 3.4169201155805724
test 7: 3.4156326550999467
test 7: 3.4091953526968184
test 7: 3.414345194619321
test 7: 3.406620431735567
test 7: 3.410482813177444
test 7: 3.418207576061198
test 7: 3.4156326550999467
test 7: 3.4091953526968184
test 7: 3.406620431735567
test 7: 3.410482813177444
test 7: 3.4169201155805724
test 7: 3.4091953526968184
test 7: 3.4117702736580697
test 7: 

test 7: 3.4091953526968184
test 7: 3.4156326550999467
test 7: 3.406620431735567
test 7: 3.4156326550999467
test 7: 3.410482813177444
test 7: 3.4091953526968184
test 7: 3.4117702736580697
test 7: 3.410482813177444
test 7: 3.410482813177444
test 7: -5.579853723031726
test 7: -5.590153406876731
test 7: -5.586291025434854
test 7: -5.582428643992977
test 7: -5.586291025434854
test 7: -5.585003564954229
test 7: -5.577278802070475
test 7: -5.5785662625511
test 7: -5.581141183512352
test 7: -5.581141183512352
test 7: -5.583716104473603
test 7: -5.586291025434854
test 7: -5.588865946396106
test 7: -5.583716104473603
test 7: -5.575991341589849
test 7: -5.579853723031726
test 7: -5.583716104473603
test 7: -5.579853723031726
test 7: -5.586291025434854
test 7: -5.582428643992977
test 7: -5.581141183512352
test 7: -5.583716104473603
test 7: -5.586291025434854
test 7: 3.406620431735567
test 7: 3.4156326550999467
test 7: 3.422069957503075
test 7: 3.4079078922161927
test 7: 3.410482813177444
test 7: 3.

test 7: 3.4130577341386954
test 7: 3.410482813177444
test 7: 3.4156326550999467
test 7: 3.418207576061198
test 7: 3.4169201155805724
test 7: 3.4156326550999467
test 7: 3.4117702736580697
test 7: 3.414345194619321
test 7: 3.410482813177444
test 7: 3.4130577341386954
test 7: 3.4156326550999467
test 7: 3.410482813177444
test 7: 3.4091953526968184
test 7: 3.406620431735567
test 7: -4.074812421180298
test 7: -5.582428643992977
test 7: -5.583716104473603
test 7: -5.586291025434854
test 7: -5.575991341589849
test 7: -5.577278802070475
test 7: -5.582428643992977
test 7: -5.588865946396106
test 7: -5.586291025434854
test 7: -5.586291025434854
test 7: -5.586291025434854
test 7: -5.581141183512352
test 7: -5.579853723031726
test 7: -5.590153406876731
test 7: -5.590153406876731
test 7: -5.586291025434854
test 7: -5.583716104473603
test 7: -5.586291025434854
test 7: -5.583716104473603
test 7: -5.585003564954229
test 7: -5.582428643992977
test 7: 3.4130577341386954
test 7: 3.4130577341386954
test 7:

test 7: 3.410482813177444
test 7: 3.4169201155805724
test 7: 3.410482813177444
test 7: 3.4117702736580697
test 7: 3.4130577341386954
test 7: 3.4130577341386954
test 7: 3.4091953526968184
test 7: 3.4156326550999467
test 7: 3.410482813177444
test 7: 3.4156326550999467
test 7: 3.4130577341386954
test 7: -5.586291025434854
test 7: -5.586291025434854
test 7: -5.588865946396106
test 7: -5.583716104473603
test 7: -5.579853723031726
test 7: -5.579853723031726
test 7: -5.582428643992977
test 7: -5.588865946396106
test 7: -5.585003564954229
test 7: -5.583716104473603
test 7: -5.581141183512352
test 7: -5.582428643992977
test 7: -5.579853723031726
test 7: -5.583716104473603
test 7: -5.586291025434854
test 7: -5.583716104473603
test 7: -5.582428643992977
test 7: -5.583716104473603
test 7: -5.583716104473603
test 7: -5.588865946396106
test 7: -5.579853723031726
test 7: -5.577278802070475
test 7: 3.4156326550999467
test 7: 3.4079078922161927
test 7: 3.4156326550999467
test 7: 3.4091953526968184
test

KeyboardInterrupt: 